In [2]:
#pip install torch --upgrade.  
# Comment: earlier versions of my program did not work because there was an error in Pytorch and this wasted days of my time
# So make sure the most updated version!                
           
import torch                                         # imports the core PyTorch library
import torch.nn as nn                                # torch.nn library is a high-level interface for building and training neural networks
import torch.optim as optim                          # Needed for optimizer
from torch.utils.data import DataLoader              # Needed for loading data from MNIST png files
from torchvision import datasets, transforms         # Needed for making sure data from MNIST png files is properly formatted 
import torch.nn.functional as F                      # Needed for functional equation in forward loop
import numpy as np                                   # Needed for outputting weights and biases
from torchvision.datasets import VisionDataset       # VisionDataset is is designed to be a base class for datasets in computer vision tasks
from PIL import Image                                # Needed for manipulating MNIST png image files 
import os                                            # Needed for operating system for dealing with dir of training and test png files

# Set the device
device = "mps" if torch.backends.mps.is_available() else "cpu"
# Check PyTorch has access to MPS (Metal Performance Shader, Apple's GPU architecture)
print(f"Is MPS (Metal Performance Shader) built? {torch.backends.mps.is_built()}")

Is MPS (Metal Performance Shader) built? True


In [35]:
class CustomMNIST(VisionDataset):          
    def __init__(self, root, train=True, transform=None, target_transform=None):
        super(CustomMNIST, self).__init__(root, transform=transform, target_transform=target_transform)

        self.train = train
        self.data_folder = "training" if train else "testing"
        self.images_folder = os.path.join(self.root, self.data_folder)

        self.image_paths = self._get_image_paths()

    def _get_image_paths(self):
        image_paths = []
        for digit_folder in os.listdir(self.images_folder):
            digit_folder_path = os.path.join(self.images_folder, digit_folder)
            
            # Check if it's a directory before listing its contents
            if os.path.isdir(digit_folder_path):
                for image_name in os.listdir(digit_folder_path):
                    image_path = os.path.join(digit_folder_path, image_name)
                    image_paths.append((image_path, int(digit_folder)))

        return image_paths
    
    def __getitem__(self, index):
        image_path, label = self.image_paths[index]

        # Skip files with the '.DS_Store' extension
        if image_path.endswith('.DS_Store'):
            return self.__getitem__(index + 1)

        image = Image.open(image_path).convert("L")

        if self.transform is not None:
            image = self.transform(image)

        return image, label

    def __len__(self):
        return len(self.image_paths)

In [36]:
# Define transformations for the dataset
transform = transforms.Compose([
    transforms.Grayscale(num_output_channels=1),  # Convert to grayscale
    transforms.Resize((28, 84)),                  # Resize images to 28x28
    transforms.ToTensor(),
])

In [37]:
# Split the dataset into training and validation sets
# Download the MNIST PNG files to your Desktop from this site: https://github.com/DeepLenin/fashion-mnist_png/tree/master
# I downloaded the data.zip file
# In this example, the files should be in PNG format

mnist_dataset = CustomMNIST(root='/Users/peternoble/Desktop/mnist_png', train=True, transform=transform)
train_size = int(0.8 * len(mnist_dataset))
val_size = len(mnist_dataset) - train_size
train_dataset, val_dataset = torch.utils.data.random_split(mnist_dataset, [train_size, val_size])

In [38]:
# Create data loaders
train_loader = torch.utils.data.DataLoader(train_dataset, batch_size=32, shuffle=True) 
val_loader = torch.utils.data.DataLoader(val_dataset, batch_size=32, shuffle=False)   

In [39]:
# Print the size of the training and validation datasets
print(f'Training dataset size: {len(train_loader.dataset)}')
print(f'Validation dataset size: {len(val_loader.dataset)}')

Training dataset size: 48008
Validation dataset size: 12002


In [40]:
# Set the path where you want to save the images. Useful for visualizing the actual images used for validation
output_path = '/Users/peternoble/Desktop/valid'
# Ensure the output directory exists
os.makedirs(output_path, exist_ok=True)
# Variables to store all images and labels
all_images = []
all_labels = []

# Iterate through the validation loader and concatenate images and labels
for batch_idx, (images, labels) in enumerate(val_loader):
    all_images.append(images)
    all_labels.append(labels)

# Concatenate the lists to get all images and labels
all_images = torch.cat(all_images, dim=0)
all_labels = torch.cat(all_labels, dim=0)

# Define a function to save images
def save_images(images, labels, output_path):
    for i in range(len(images)):
        image, label = images[i], labels[i]
        # Assuming the images are in the range [0, 1], and using torchvision to convert to PIL
        image_pil = transforms.ToPILImage()(image)
        image_pil.save(os.path.join(output_path, f"image_{i}_label_{label}.png"))

# Save all images from the validation dataset
save_images(all_images, all_labels, output_path)

In [ ]:
class SimpleModel(nn.Module):
    def __init__(self):
        super(SimpleModel, self).__init__()
        self.conv1 = nn.Conv2d(in_channels=1, out_channels=64, kernel_size=2, stride=1, padding=1)
        self.pool = nn.MaxPool2d(kernel_size=2, stride=2)
        self.flatten = nn.Flatten()
        self.fc1 = nn.Linear(64 * 14 * 42, 10)    # out_channels == first number in  self.fc1 = nn.Linear(here...
 
    def forward(self, x):
        x = self.pool(F.relu(self.conv1(x)))
        x = self.flatten(x)
        x = self.fc1(x)
        return x
       
# Initialize the model
model = SimpleModel()

# Define loss function and optimizer
criterion = nn.CrossEntropyLoss()
optimizer = optim.Adam(model.parameters(), lr=0.001)

# Training loop
num_epochs = 1                                         # Adjust the number of epochs as needed

for epoch in range(num_epochs):
    model.train()                                      # Set the model to training mode
    running_loss = 0.0

    # Iterate over the training dataset
    for inputs, labels in train_loader:
        optimizer.zero_grad()                          # Zero the gradients
        # Forward pass
        outputs = model(inputs)
        # Compute the loss
        loss = criterion(outputs, labels)
        # Backward pass
        loss.backward()
        # Update the parameters
        optimizer.step()
        running_loss += loss.item()

    # Print the average loss for the epoch
    average_loss = running_loss / len(train_loader)
    print(f"Epoch {epoch + 1}/{num_epochs}, Loss: {average_loss}")

# Training complete
print("Finished Training")

In [ ]:
# Save the model state_dict
torch.save(model.state_dict(), '64_1_model.pth')

In [ ]:
# Assuming you have a validation DataLoader named val_loader
#loaded_model = SimpleModel()
#loaded_model.load_state_dict(torch.load('64_1_model.pth'))
#loaded_model.eval() 

model.eval()                                          # Set the model to evaluation mode
all_predictions = []
all_labels = []                                       # This list was missing in the original code

with torch.no_grad():
    for inputs, labels in val_loader:
        try:
            # Ensure the input size is correct
            inputs = inputs.view(inputs.size(0), 1, 28, 84)

            outputs = model(inputs)
            predictions = torch.argmax(outputs, dim=1)
            all_predictions.extend(predictions.tolist())
            all_labels.extend(labels.tolist())  # Populate the true labels
        except Exception as e:
            print(f"An error occurred: {e}")

# Now you have lists of all predicted labels and true labels
# You can compare them to compute accuracy or analyze the classification breakdown

# Compute accuracy
if len(all_labels) > 0:
    accuracy = sum(p == l for p, l in zip(all_predictions, all_labels)) / len(all_labels)
    print(f"Accuracy: {accuracy:.2%}")
else:
    print("No labels available for computing accuracy.")

# Analyze classification breakdown
for digit in range(10):
    correct = sum(p == digit and l == digit for p, l in zip(all_predictions, all_labels))
    total = all_labels.count(digit)
    
    if total == 0:
        print(f"Digit {digit}: No examples in the validation set")
    else:
        percentage = correct / total if total != 0 else 0.0
        print(f"Digit {digit}: Correctly classified {correct}/{total} ({percentage:.2%})")


In [ ]:
# Assuming you have a validation DataLoader named val_loader
loaded_model = SimpleModel()

model.eval()  # Set the model to evaluation mode
params = list(loaded_model.parameters())
print(params[0].shape)
print(params[1].shape)
print(params[2].shape)
print(params[3].shape)

flattened_weights = params[0].data.flatten()
np.savetxt('weights_0.txt', flattened_weights)

flattened_weights1 = params[1].data.flatten()
np.savetxt('biases_0.txt', flattened_weights1)
print (flattened_weights1)
flattened_weights2 = params[2].data.flatten()
np.savetxt('weights_1.txt', flattened_weights2)

flattened_weights3 = params[3].data.flatten()
np.savetxt('biases_1.txt', flattened_weights3)

# Print the weights and biases
for name, param in loaded_model.named_parameters():
    if 'weight' in name or 'bias' in name:
        print(f"Parameter: {name}, Shape: {param.shape}")
        print("Values:")
        print(param.data)
        print("\n")